# **multimoda-rs**: Tutorial examples IVUS/OCT to centerline
## Alining from files
The first example will focus on solving the problem of aligning frames within a pullback of either IVUS or OCT images.
We will start with gated IVUS images (systole/diastole) during two different states (e.g. rest/stress).
The .csv files are expected to set up in the following style:
```text
--------------------------------------------------------------------
|      185     |       5.32     |      2.37       |        0.0     |
|      185     |       5.12     |      2.46       |        0.0     |
|      ...     |       ...      |      ...        |        ...     |
```
where the first column is the frame index the point is from, the second to forth are x-, y- and z-coordinates. The naming conventions of the files are diastolic_contours.csv, diastolic_reference_points.csv, ... (see ./data). This is in alignment with the output of the [AIVUS-CAA software](https://https://github.com/AI-in-Cardiovascular-Medicine/AIVUS-CAA).

The first goal is to align the frames within a pullback by translating their centroids to a line and rotating them towards each other minimizing Hausdorff distance of the contours and catheter contours created from the image center. The influence of the catheter (which represents the image center) on the rotation can be adjusted by the number of points passed to catheter. If no catheter should be created just pass n_points=0.

In the same function states are aligned with each other (e.g. systole to diastole) and z-distance are averaged over the two states to have comparable frame positions. If heartrate is very different (e.g. rest to stress) a resampling is performed of the lower heartrate geometry.

Load packages multimodars, and for linking the numpy package.

In [3]:
import os
from pathlib import Path
import numpy as np
import multimodars as mm

# load the provided example data
os.chdir(Path.cwd().parent / "data")

# mode full compares diastole to systole for rest and stress conditions
rest, stress, dia, sys, _ = mm.from_file(
    mode="full", 
    input_path_a="ivus_rest", 
    input_path_b="ivus_stress",
    label="full",
    step_rotation_deg=0.1, 
    range_rotation_deg=90, 
    output_path_a="output/rest", 
    output_path_b="output/stress", 
    output_path_c="output/diastole", 
    output_path_d="output/systole", 
    write_obj=True,
    watertight=False, # creates shell
    interpolation_steps=28, 
    image_center=(4.5, 4.5),
    radius=0.5,
    n_points=20,
    contour_types=[mm.PyContourType.Lumen, mm.PyContourType.Catheter, mm.PyContourType.Wall]
)

# preparing raw data to plot for comparison
rest_dia = np.genfromtxt("ivus_rest/diastolic_contours.csv")
rest_dia_ref_point = np.genfromtxt("ivus_rest/diastolic_reference_points.csv")
rest_sys= np.genfromtxt("ivus_rest/systolic_contours.csv")
rest_sys_ref_point = np.genfromtxt("ivus_rest/systolic_reference_points.csv")

rest_dia_geom_before = mm.numpy_to_geometry(
    lumen_arr=rest_dia,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=rest_dia_ref_point,
    label="unprocessed_dia",
)
new_frames_a = []
for frame in rest_dia_geom_before.frames:
    cont = frame.sort_frame_points()
    new_frames_a.append(cont)
rest_dia_geom_before.frames = np.array(new_frames_a)

rest_sys_geom_before = mm.numpy_to_geometry(
    lumen_arr=rest_sys,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=rest_sys_ref_point,
    label="unprocessed_sys",
)
new_frames_b = []
for frame in rest_sys_geom_before.frames:
    cont = frame.sort_frame_points()
    new_frames_b.append(cont)
rest_sys_geom_before.frames = np.array(new_frames_b)

mm.to_obj(rest_dia_geom_before, "output/unprocessed", watertight=False, contour_types=[mm.PyContourType.Lumen], filename_prefix="dia")
mm.to_obj(rest_sys_geom_before, "output/unprocessed", watertight=False, contour_types=[mm.PyContourType.Lumen], filename_prefix="sys")


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systolic
Diastole phase: No


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systolic
Diastole phase: No

Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previ

calcification file not found, skipping: "ivus_rest/calcium_diastolic_contours.csv"
sidebranch file not found, skipping: "ivus_rest/branch_diastolic_contours.csv"
eem file not found, skipping: "ivus_rest/eem_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
eem file not found, skipping: "ivus_rest/eem_systolic_contours.csv"
calcification file not found, skipping: "ivus_rest/calcium_systolic_contours.csv"
sidebranch file not found, skipping: "ivus_rest/branch_systolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
eem file not found, skipping: "ivus_stress/eem_diastolic_contours.csv"
sidebranch file not found, skipping: "ivus_stress/branch_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
calcification file not found, skipping: "ivus_stress/calcium_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
calcification file not found, skipping: "ivus_stress/calcium

Successfully wrote lumen to output/unprocessed/dia_lumen.obj
Successfully wrote lumen to output/unprocessed/sys_lumen.obj


In [4]:
# Install if needed
%pip install trimesh plotly

# Imports
import trimesh
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def trimesh_to_mesh3d(mesh, color, name):
    """
    Convert a trimesh.Trimesh to a Plotly Mesh3d trace.
    """
    # get vertices and faces
    verts = mesh.vertices
    faces = mesh.faces
    return go.Mesh3d(
        x=verts[:,0], y=verts[:,1], z=verts[:,2],
        i=faces[:,0], j=faces[:,1], k=faces[:,2],
        color=color, opacity=0.6,
        name=name,
        flatshading=True
    )

def plot_pair(before_paths, after_paths, colors, titles):
    """
    before_paths, after_paths: list of two .obj file paths [dia, sys]
    colors: list of two colors (e.g. ['blue','red'])
    titles: [left_title, right_title]
    """
    before_meshes = [trimesh.load(p) for p in before_paths]
    after_meshes  = [trimesh.load(p) for p in after_paths]

    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{"type":"scene"}, {"type":"scene"}]],
        subplot_titles=titles
    )

    for mesh, color, label in zip(before_meshes, colors, ["diastole","systole"]):
        fig.add_trace(
            trimesh_to_mesh3d(mesh, color, f"before_{label}"),
            row=1, col=1
        )
    for mesh, color, label in zip(after_meshes, colors, ["diastole","systole"]):
        fig.add_trace(
            trimesh_to_mesh3d(mesh, color, f"after_{label}"),
            row=1, col=2
        )

    # link camera on both scenes
    camera = dict(
        eye=dict(x=1.5, y=1.5, z=1.0)
    )
    fig.update_layout(
        width=900, height=450,
        # apply same camera to both
        scene_camera=camera,
        scene2_camera=camera,
        # enforce equal scaling on x/y/z for both subplots
        scene=dict(
            aspectmode="data"
        ),
        scene2=dict(
            aspectmode="data"
        ),
        margin=dict(l=0, r=0, t=30, b=0)
    )
    fig.show()

# Paths “before” geometries
before_paths = [
    "output/unprocessed/rest_dia.obj",
    "output/unprocessed/rest_sys.obj",
]

# Paths “after” (processed) meshes
after_paths = [
    "output/rest/lumen_000_full.obj",    # diastole post
    "output/rest/lumen_029_full.obj",    # systole post
]

colors = ["royalblue", "firebrick"]

titles = ["Before Processing", "After Processing"]

plot_pair(before_paths, after_paths, colors, titles)

Note: you may need to restart the kernel to use updated packages.


The data is now neatly ordered in pairs (e.g. diastolic and systolic geometry). Every geometry has contours for lumen and walls and a created catheter. The reference point will be used to align the geometry to the centerline. All points corresponding to a contour are also save in a contour struct.

In [5]:
print(f"Example of PyGeometryPair:\n{rest}")
print(f"Example of PyGeometry:\n{rest.geom_a}")
print(f"Example of PyFrame:\n{rest.geom_a.frames[0]}")
print(f"Example of PyContour:\n{rest.geom_a.frames[0].lumen}")
print(f"Example of PyContourPoint:\n{rest.geom_a.frames[0].lumen.points[0]}")


Example of PyGeometryPair:
GeometryPair full - full (diastolic: 14 frames, systolic: 14 frames)
Example of PyGeometry:
Geometry(14 frames, label='full')
Example of PyFrame:
Frame(id=0, centroid=(3.72, 5.25, 0.00), lumen=Contour(id=0, frame=385, points=501, centroid=(3.72, 5.25, 0.00), kind=Lumen), extras=2)
Example of PyContour:
Contour(id=0, frame=385, points=501, centroid=(3.72, 5.25, 0.00), kind=Lumen)
Example of PyContourPoint:
Point(frame_id=19, pt_id=0, x=3.80, y=7.90, z=0.00, aortic=false)


Additionally is it possible to get different measurements, regarding stenosis, directly from the objects now:

In [8]:
# Summary over PyGeometryPair
print(f"Summary over PyGeometryPair object (dia_geom: (mla [mm^2], max. stenosis, stenosis length [mm]), sys_geom...):\n{rest.get_summary()[0]}\n \
      table (contour id, diastolic area, diastolic elliptic ratio, systolic area, systolic elliptic ratio, z coordinates):\n{np.array(rest.get_summary()[1])}")
# Summary over PyGeometry
print(f"PyGeometry (mla [mm^2], max. stenosis, stenosis length [mm]):\n {rest.geom_a.get_summary()}")
# or more specific per contour
print(rest.geom_a.frames[0].lumen.get_area())
print(rest.geom_a.frames[-1].lumen.get_elliptic_ratio())

+----+----------+-----------+----------+-----------+-------+
| id | area_dia | ellip_dia | area_sys | ellip_sys |   z   |
+----+----------+-----------+----------+-----------+-------+
| 0  | 5.64     | 4.59      | 6.11     | 4.35      | 0.00  |
| 1  | 5.80     | 4.75      | 6.26     | 3.39      | 1.30  |
| 2  | 5.70     | 3.70      | 6.49     | 2.85      | 2.59  |
| 3  | 5.56     | 2.57      | 6.85     | 2.18      | 3.89  |
| 4  | 5.59     | 1.64      | 7.59     | 1.91      | 5.18  |
| 5  | 6.42     | 1.51      | 7.57     | 1.68      | 6.48  |
| 6  | 7.26     | 1.37      | 7.31     | 1.63      | 7.77  |
| 7  | 7.74     | 1.25      | 10.23    | 1.33      | 9.07  |
| 8  | 7.77     | 1.43      | 11.90    | 1.20      | 10.36 |
| 9  | 9.05     | 1.33      | 14.15    | 1.09      | 11.66 |
| 10 | 11.92    | 1.18      | 11.70    | 1.17      | 12.96 |
| 11 | 15.27    | 1.08      | 13.57    | 1.15      | 14.25 |
| 12 | 17.27    | 1.06      | 15.42    | 1.11      | 15.55 |
| 13 | 16.34    | 1.04  


The four pairs represent all 4 possible comparison in gated images, as for example in coronary artery anomalies (rest pulsatile lumen deformation, stress pulsatile lumen deformation, stress-induced diastolic lumen deformation and stress-induced systolic lumen deformation). See also paper:

<img src="../paper/figures/Figure1.jpg" alt="States figure" width="500"/>

The idea behind the interpolation steps, is to provide a set of geometries that can be used to render a video of the compression over time (e.g. in blender, see the example script). Blender allows for an easy open sourec solution. Just navigate to the directory, and run blender with context:
```bash
cd '.\Program Files\Blender Foundation\Blender 4.4\'
.\blender.exe -con 
```
Then just copy/paste the script in the `Scripting` tab and run it. The result will look something like this:
<img src="../paper/figures/animation_stress_induced_systolic_deformation.gif" alt="Deformation Gif" width="500"/>

Scripts can be adjusted to individual need. If no animations are planned interpolation steps can just be set to 0.

## Coronary Artery Disease Case
So far we only did dynamic comparison in coronary artery disease. However `multimodars`can also be used to reconstruct single cases with coronary artery
disease and then reconstruct the different layers (catheter, lumen, eem and wall)
to create a 3D model of the stenosis.

In [10]:
cad, _ = mm.from_file(
    mode="single", 
    input_path="ivus_full",
    label="cad",
    diastole=True,
    step_rotation_deg=0.1, 
    range_rotation_deg=90, 
    output_path="output/cad",
    write_obj=True,
    watertight=False, # creates shell
    interpolation_steps=0, 
    image_center=(4.5, 4.5),
    radius=0.5,
    n_points=20,
    contour_types=[mm.PyContourType.Lumen, mm.PyContourType.Eem, mm.PyContourType.Catheter, mm.PyContourType.Wall]
)
cad_aligned = cad.center_to_contour(mm.PyContourType.Eem)
mm.to_obj(cad_aligned, "output/cad", watertight=False, contour_types=[mm.PyContourType.Lumen, mm.PyContourType.Eem, mm.PyContourType.Catheter, mm.PyContourType.Wall], filename_prefix="aligned")

# cell – comparison of post-processing meshes
import trimesh
import plotly.graph_objects as go
from plotly.subplots import make_subplots 

# reuse the helper from before
def trimesh_to_mesh3d(mesh, color, name, opacity):
    verts = mesh.vertices
    faces = mesh.faces
    return go.Mesh3d(
        x=verts[:,0], y=verts[:,1], z=verts[:,2],
        i=faces[:,0], j=faces[:,1], k=faces[:,2],
        color=color, opacity=opacity,
        name=name,
        flatshading=True
    )

# load the two meshes
lumen = trimesh.load("output/cad/lumen_cad.obj")
eem = trimesh.load("output/cad/eem_cad.obj")
wall = trimesh.load("output/cad/wall_cad.obj")
lumen_aligned = trimesh.load("output/cad/aligned_lumen.obj")
eem_aligned = trimesh.load("output/cad/aligned_eem.obj")
wall_aligned = trimesh.load("output/cad/aligned_wall.obj")

# create traces
trace_lumen = trimesh_to_mesh3d(lumen, 'firebrick', 'Lumen', 1.0)
trace_eem = trimesh_to_mesh3d(eem, 'royalblue', 'External Elastic Membrane', 0.6)
trace_wall = trimesh_to_mesh3d(wall, 'white', 'Coronary Wall', 0.5)
trace_lumen_aligned = trimesh_to_mesh3d(lumen_aligned, 'firebrick', 'Lumen', 1.0)
trace_eem_aligned = trimesh_to_mesh3d(eem_aligned, 'royalblue', 'External Elastic Membrane', 0.6)
trace_wall_aligned = trimesh_to_mesh3d(wall_aligned, 'white', 'Coronary Wall', 0.5)

# Create a subplot layout with 2 scenes side-by-side
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'scene'}, {'type': 'scene'}]],
    subplot_titles=("Original CAD Mesh", "Aligned CAD Mesh")
)

# Add traces to respective subplots
fig.add_trace(trace_lumen, row=1, col=1)
fig.add_trace(trace_eem, row=1, col=1)
fig.add_trace(trace_wall, row=1, col=1)

fig.add_trace(trace_lumen_aligned, row=1, col=2)
fig.add_trace(trace_eem_aligned, row=1, col=2)
fig.add_trace(trace_wall_aligned, row=1, col=2)

# Set up camera
camera = dict(eye=dict(x=1.5, y=1.5, z=1.0))

# Layout updates
fig.update_layout(
    # title_text="CAD Mesh Comparison: Original vs. Aligned",
    width=900, height=450,
    scene=dict(
        camera=camera,
        aspectmode='data',
        xaxis_title="X", yaxis_title="Y", zaxis_title="Z"
    ),
    scene2=dict(
        camera=camera,
        aspectmode='data',
        xaxis_title="X", yaxis_title="Y", zaxis_title="Z"
    ),
    margin=dict(l=0, r=0, t=40, b=0)
)

fig.show()


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
✅ Eem
✅ Calcification
✅ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes

Aligning Frame 1 to previous Frame 0
Aligning Frame 2 to previous Frame 1
Aligning Frame 3 to previous Frame 2
Aligning Frame 4 to previous Frame 3
Aligning Frame 5 to previous Frame 4
Aligning Frame 6 to previous Frame 5
Aligning Frame 7 to previous Frame 6
Aligning Frame 8 to previous Frame 7
Aligning Frame 9 to previous Frame 8
Aligning Frame 10 to previous Frame 9
Aligning Frame 11 to previous Frame 10
Aligning Frame 12 to previous Frame 11
Aligning Frame 13 to previous Frame 12
Aligning Frame 14 to previous Frame 13
Aligning Frame 15 to previous Frame 14
Aligning Frame 16 to previous Frame 15
Aligning Frame 17 to previous Frame 16
Aligning Frame 18 to previous Frame 17
Aligning Frame 19 to previous Frame 18
Aligning Frame 20 to previous Frame 19
Aligning Frame 21 to p

process_directory: unknown mapping name 'catheter', skipping


## Stent example
This can also be used for pre-and post-stenting comparison (here example of stenting an intramural course of a coronary artery anomaly):

In [12]:
_, _, dia, sys, _ = mm.from_file(
    mode="full",
    label="stent",
    input_path_a="ivus_prestent",
    input_path_b="ivus_poststent",
    output_path_a="output/stent_rest",
    output_path_b="output/stent_stress",
    output_path_c="output/stent_diastole",
    output_path_d="output/stent_systole",
    steps_best_rotation=0.1,
    range_rotation_deg=45,
    interpolation_steps=0,
    watertight=False,
    )

# cell – comparison of post-processing meshes
import trimesh
import plotly.graph_objects as go

# reuse the helper from before
def trimesh_to_mesh3d(mesh, color, name):
    verts = mesh.vertices
    faces = mesh.faces
    return go.Mesh3d(
        x=verts[:,0], y=verts[:,1], z=verts[:,2],
        i=faces[:,0], j=faces[:,1], k=faces[:,2],
        color=color, opacity=0.6,
        name=name,
        flatshading=True
    )

# load the two meshes
mesh_dia = trimesh.load("output/stent_diastole/lumen_000_stent.obj")
mesh_sys = trimesh.load("output/stent_diastole/lumen_001_stent.obj")

# create traces
trace_dia = trimesh_to_mesh3d(mesh_dia, 'royalblue', 'Before (mesh_000)')
trace_sys = trimesh_to_mesh3d(mesh_sys, 'firebrick', 'After (mesh_001)')

# define a canonical camera position
camera = dict(eye=dict(x=1.5, y=1.5, z=1.0))

# build and show figure
fig = go.Figure(data=[trace_dia, trace_sys])
fig.update_layout(
    title="Post-processing: Prestenting vs Poststenting",
    width=600, height=600,
    scene=dict(
        aspectmode="data",    # equal scales on x/y/z
        camera=camera,
        xaxis_title="X",
        yaxis_title="Y",
        zaxis_title="Z"
    ),
    margin=dict(l=0, r=0, t=30, b=0)
)
fig.show()


sidebranch file not found, skipping: "ivus_prestent/branch_diastolic_contours.csv"
calcification file not found, skipping: "ivus_prestent/calcium_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
eem file not found, skipping: "ivus_prestent/eem_diastolic_contours.csv"
eem file not found, skipping: "ivus_prestent/eem_systolic_contours.csv"
calcification file not found, skipping: "ivus_prestent/calcium_systolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
sidebranch file not found, skipping: "ivus_prestent/branch_systolic_contours.csv"
eem file not found, skipping: "ivus_poststent/eem_diastolic_contours.csv"
sidebranch file not found, skipping: "ivus_poststent/branch_diastolic_contours.csv"
calcification file not found, skipping: "ivus_poststent/calcium_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
eem file not found, skipping: "ivus_poststent/eem_systolic_contours.csv"
process_directo


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systolic
Diastole phase: No


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systolic
Diastole phase: No

Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previ

However, for these pre- and poststenting comparisons the original from_file approach is computationally more expensive, than using the more flexible .from_array() approach:

In [13]:
before_arr = np.genfromtxt("ivus_prestent/diastolic_contours.csv", delimiter='\t')
before_ref = np.genfromtxt("ivus_prestent/diastolic_reference_points.csv", delimiter='\t')
after_arr = np.genfromtxt("ivus_poststent/diastolic_contours.csv", delimiter='\t')
after_ref = np.genfromtxt("ivus_poststent/diastolic_reference_points.csv", delimiter='\t')

before_geom = mm.numpy_to_geometry(
    lumen_arr=before_arr,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=before_ref,
)
after_geom = mm.numpy_to_geometry(
    lumen_arr=after_arr,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=after_ref,
)
contours = []
ref_pt = None
for frame in before_geom.frames:
    contours.append(frame.lumen)
    if frame.reference_point is not None:
        ref_pt = frame.reference_point

before_input_data = mm.PyInputData(
    lumen=contours,
    eem=None,
    calcification=None,
    sidebranch=None,
    record=None,
    ref_point=ref_pt,
    diastole=True,
    label="oct"
)

contours = []
ref_pt = None
for frame in after_geom.frames:
    contours.append(frame.lumen)
    if frame.reference_point is not None:
        ref_pt = frame.reference_point

after_input_data = mm.PyInputData(
    lumen=contours,
    eem=None,
    calcification=None,
    sidebranch=None,
    record=None,
    ref_point=ref_pt,
    diastole=True,
    label="stent"
)

pair, _ = mm.from_array(
    mode="singlepair",
    input_data_a=before_input_data,
    input_data_b=after_input_data,
    label="singlepair",
    diastole=True,
    output_path="output/stent_comparison",
    steps_best_rotation=0.01,
    range_rotation_deg=30,
)


✅ Successfully built geometry from input data
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: oct
Diastole phase: Yes


✅ Successfully built geometry from input data
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: stent
Diastole phase: Yes

Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 2 to previous Frame 1
Aligning Frame 2 to previous Frame 1
Aligning Frame 3 to previous Frame 2
Aligning Frame 3 to previous Frame 2
Aligning Frame 4 to previous Frame 3
Aligning Frame 4 to previous Frame 3
Aligning Frame 5 to previous Frame 4
Aligning Frame 5 to previous Frame 4
Aligning Frame 6 to previous Frame 5
Aligning Frame 6 to previous Frame 5
Aligning Frame 7 to previous Frame 6
Aligning Frame 7 to previous Frame 6
Aligning Frame 8 to previous Frame 7
Aligning 

Or you can reconstruct a a single 3D geometry from OCT for example.

In [11]:
oct_raw = np.genfromtxt("oct_single/oct_contours_raw.csv", delimiter=',')
oct_ref = np.genfromtxt("oct_single/oct_ref.csv", delimiter=',')
oct_geom = mm.numpy_to_geometry(
    lumen_arr=oct_raw,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=oct_ref,
)
contours = []
ref_pt = None
for frame in oct_geom.frames:
    contours.append(frame.lumen)
    if frame.reference_point is not None:
        ref_pt = frame.reference_point

oct_input_data = mm.PyInputData(
    lumen=contours,
    eem=None,
    calcification=None,
    sidebranch=None,
    record=None,
    ref_point=ref_pt,
    diastole=True,
    label="oct"
)

oct_recon, _ = mm.from_array(
    mode="single",
    input_data=oct_input_data,
    label="oct",
    diastole=True,
    step_rotation_deg=0.01,
    range_rotation_deg=6,
    image_center=(5.0, 5.0),
    radius=0.5,
    n_points=40,
    write_obj=False,
    output_path="data/output/oct",
    watertight=False,
    smooth=False,
)


✅ Successfully built geometry from input data
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: oct
Diastole phase: Yes

Aligning Frame 1 to previous Frame 0
Aligning Frame 2 to previous Frame 1
Aligning Frame 3 to previous Frame 2
Aligning Frame 4 to previous Frame 3
Aligning Frame 5 to previous Frame 4
Aligning Frame 6 to previous Frame 5
Aligning Frame 7 to previous Frame 6
Aligning Frame 8 to previous Frame 7
Aligning Frame 9 to previous Frame 8
Aligning Frame 10 to previous Frame 9
Aligning Frame 11 to previous Frame 10
Aligning Frame 12 to previous Frame 11
Aligning Frame 13 to previous Frame 12
Aligning Frame 14 to previous Frame 13
Aligning Frame 15 to previous Frame 14
Aligning Frame 16 to previous Frame 15
Aligning Frame 17 to previous Frame 16
Aligning Frame 18 to previous Frame 17
Aligning Frame 19 to previous Frame 18
Aligning Frame 20 to previous Frame 19
Aligning Frame 21 to p

## Alignment from array
While the alignment from file is one option, the more flexible option is to create Geometries directly from numpy array, and then perform the same operations with these Geometries. It is enough to provide contour coordinates and a reference point for the different states that should be compared.

In [12]:
dia_cont = np.genfromtxt("fixtures/idealized_geometry/diastolic_contours.csv", delimiter=',')
dia_ref = np.genfromtxt("fixtures/idealized_geometry/diastolic_reference_points.csv", delimiter=',')

sys_cont = np.genfromtxt("fixtures/idealized_geometry/systolic_contours.csv", delimiter=',')
sys_ref = np.genfromtxt("fixtures/idealized_geometry/systolic_reference_points.csv", delimiter=',')

rest_dia = mm.numpy_to_geometry(
    lumen_arr=dia_cont,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=dia_ref,
)

rest_sys = mm.numpy_to_geometry(
    lumen_arr=sys_cont,
    eem_arr=np.array([]),
    catheter_arr=np.array([]),
    wall_arr=np.array([]),
    reference_arr=sys_ref,
)
contours = []
ref_pt = None
for frame in rest_dia.frames:
    contours.append(frame.lumen)
    if frame.reference_point is not None:
        ref_pt = frame.reference_point

rest_dia_input_data = mm.PyInputData(
    lumen=contours,
    eem=None,
    calcification=None,
    sidebranch=None,
    record=None,
    ref_point=ref_pt,
    diastole=True,
    label="diastole"
)

contours = []
ref_pt = None
for frame in rest_sys.frames:
    contours.append(frame.lumen)
    if frame.reference_point is not None:
        ref_pt = frame.reference_point

rest_sys_input_data = mm.PyInputData(
    lumen=contours,
    eem=None,
    calcification=None,
    sidebranch=None,
    record=None,
    ref_point=ref_pt,
    diastole=True,
    label="systole"
)
# Actual function call
rest, (dia_logs, sys_logs) = mm.from_array(
    mode="singlepair",
    input_data_a=rest_dia_input_data,
    input_data_b=rest_sys_input_data,
    label="singlepair",
    _diastole=False,
    step_rotation_deg=0.01,
    range_rotation_deg=60,
    output_path="output/rest_array",
    interpolation_steps=0,
    smooth=True,
    postprocessing=True,
)



✅ Successfully built geometry from input data
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastole
Diastole phase: Yes


✅ Successfully built geometry from input data
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systole
Diastole phase: Yes

Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 2 to previous Frame 1
Aligning Frame 2 to previous Frame 1
Aligning Frame 3 to previous Frame 2
Aligning Frame 3 to previous Frame 2
Aligning Frame 4 to previous Frame 3
Aligning Frame 4 to previous Frame 3
Aligning Frame 5 to previous Frame 4
Aligning Frame 5 to previous Frame 4
Aligning Frame 6 to previous Frame 5
Aligning Frame 6 to previous Frame 5
Aligning Frame 7 to previous Frame 6
Aligning Frame 7 to previous Frame 6
Aligning Frame 8 to previous Frame 7
Al

## Align with centerline
After aligning the frames within a geometry the alignment with a CCTA centerline can be performed by providing three different points. Here the example of a anomalous coronary artery where a point for the aorta one for the proximal part of the vessel and one for the distal part are provided.

<img src="./figures/Alignment3p.png" alt="Alignment figure" width="500"/>

In [14]:
import multimodars as mm

rest, (dia_logs, sys_logs) = mm.from_file(
    mode="singlepair", 
    input_path="ivus_rest",
    label="aligned",
    output_path="output/rest",
)

cl_raw = np.genfromtxt("centerline_raw.csv", delimiter=',')
cl_converted = mm.numpy_to_centerline(cl_raw)

print(cl_raw)

aligned_geometry, resampled_cl = mm.align_three_point(
    centerline=cl_converted,
    geometry_pair=rest,
    aortic_ref_pt=(12.2605, -201.3643, 1751.0554),
    upper_ref_pt=(11.7567, -202.1920, 1754.7975),
    lower_ref_pt=(15.6605, -202.1920, 1749.9655),
    write=True,
    interpolation_steps=0,
)

print(resampled_cl)

eem file not found, skipping: "ivus_rest/eem_diastolic_contours.csv"
sidebranch file not found, skipping: "ivus_rest/branch_diastolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
calcification file not found, skipping: "ivus_rest/calcium_diastolic_contours.csv"
eem file not found, skipping: "ivus_rest/eem_systolic_contours.csv"
sidebranch file not found, skipping: "ivus_rest/branch_systolic_contours.csv"
process_directory: unknown mapping name 'catheter', skipping
calcification file not found, skipping: "ivus_rest/calcium_systolic_contours.csv"
resample_centerline_by_contours: centroid_count=14, centroid_mean_spacing=Some(1.2955758552631584), centerline_length=162.20506007682988, spacing=1.295576
resample_centerline_by_contours: produced 126 points

thread '<unnamed>' panicked at src/intravascular/centerline_align/align_algorithms.rs:55:9:
Frame Index 385 does not match Centerline Point Frame Index 1
note: run with `RUST_BACKTRACE=1` environment variable t


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: diastolic
Diastole phase: Yes


✅ Successfully built geometry from path
-----------------------------------------
✅ Lumen
❌ Eem
❌ Calcification
❌ Sidebranch
✅ Catheter
-----------------------------------------
Label: systolic
Diastole phase: No

Aligning Frame 1 to previous Frame 0
Aligning Frame 1 to previous Frame 0
Aligning Frame 2 to previous Frame 1
Aligning Frame 2 to previous Frame 1
Aligning Frame 3 to previous Frame 2
Aligning Frame 3 to previous Frame 2
Aligning Frame 4 to previous Frame 3
Aligning Frame 4 to previous Frame 3
Aligning Frame 5 to previous Frame 4
Aligning Frame 5 to previous Frame 4
Aligning Frame 6 to previous Frame 5
Aligning Frame 6 to previous Frame 5
Aligning Frame 7 to previous Frame 6
Aligning Frame 7 to previous Frame 6
Aligning Frame 8 to previous Frame 7
Aligning Fram

PanicException: Frame Index 385 does not match Centerline Point Frame Index 1

In [15]:
import trimesh
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def trimesh_to_mesh3d(mesh, color, name):
    """
    Convert a trimesh.Trimesh to a Plotly Mesh3d trace.
    """
    # get vertices and faces
    verts = mesh.vertices
    faces = mesh.faces
    return go.Mesh3d(
        x=verts[:,0], y=verts[:,1], z=verts[:,2],
        i=faces[:,0], j=faces[:,1], k=faces[:,2],
        color=color, opacity=0.6,
        name=name,
        flatshading=True
    )

def plot_pair(before_paths, after_paths, colors, titles):
    """
    before_paths, after_paths: list of two .obj file paths [dia, sys]
    colors: list of two colors (e.g. ['blue','red'])
    titles: [left_title, right_title]
    """
    before_meshes = [trimesh.load(p) for p in before_paths]
    after_meshes  = [trimesh.load(p) for p in after_paths]

    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{"type":"scene"}, {"type":"scene"}]],
        subplot_titles=titles
    )

    for mesh, color, label in zip(before_meshes, colors, ["diastole","systole"]):
        fig.add_trace(
            trimesh_to_mesh3d(mesh, color, f"before_{label}"),
            row=1, col=1
        )
    for mesh, color, label in zip(after_meshes, colors, ["diastole","systole"]):
        fig.add_trace(
            trimesh_to_mesh3d(mesh, color, f"after_{label}"),
            row=1, col=2
        )

    # link camera on both scenes
    camera = dict(
        eye=dict(x=1.5, y=1.5, z=1.0)
    )
    fig.update_layout(
        width=900, height=450,
        # apply same camera to both
        scene_camera=camera,
        scene2_camera=camera,
        # enforce equal scaling on x/y/z for both subplots
        scene=dict(
            aspectmode="data"
        ),
        scene2=dict(
            aspectmode="data"
        ),
        margin=dict(l=0, r=0, t=30, b=0)
    )
    fig.show()

# Paths “before” geometries
before_paths = [
    "output/rest/mesh_000_rest.obj",
    "output/rest/mesh_029_rest.obj",
]

# Paths “after” (processed) meshes
after_paths = [
    "output/aligned/mesh_000_None.obj",    # diastole post
    "output/aligned/mesh_001_None.obj",    # systole post
]

colors = ["royalblue", "firebrick"]

titles = ["Before Alignment", "After Alignment"]

plot_pair(before_paths, after_paths, colors, titles)